In [2]:
# Install dependencies
!pip install torch-geometric
!pip install torch-scatter -f https://data.pyg.org/whl/torch-1.13.1+cu116.html
!pip install torch-sparse -f https://data.pyg.org/whl/torch-1.13.1+cu116.html


Looking in links: https://data.pyg.org/whl/torch-1.13.1+cu116.html
Looking in links: https://data.pyg.org/whl/torch-1.13.1+cu116.html


In [3]:
# Import dependencies, check versions
import torch_geometric
import pandas as pd
import torch
import os
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np
print(torch.__version__)
print(torch_geometric.__version__)
"""
Should be:
1.13.1
2.2.0
"""
pass


1.13.1
2.2.0


In [4]:
#os.environ['DATASET_PATH'] = './dataset/' # Uncomment this to add own path
is_running_from_local = 'DATASET_PATH' in os.environ
if is_running_from_local:
    print('DATA_PATH: ', os.environ['DATASET_PATH'])
    DATASET_PATH = os.environ['DATASET_PATH']
else:
    from google.colab import drive
    drive.mount('/content/drive')  # Check: !ls drive/MyDrive/
    DATASET_PATH = 'drive/MyDrive/elliptic_bitcoin_dataset/'
    print("Reading from Google Colab")
    print('DATA_PATH: ', DATASET_PATH)


DATA_PATH:  ./dataset/


In [25]:
classes = pd.read_csv(
    f"{DATASET_PATH}/elliptic_bitcoin_dataset/elliptic_txs_classes.csv", index_col="txId")
edgelist = pd.read_csv(
    f"{DATASET_PATH}/elliptic_bitcoin_dataset/elliptic_txs_edgelist.csv")

# index is on top level timestamp, second level txId
features = pd.read_csv(
    f"{DATASET_PATH}/elliptic_bitcoin_dataset/elliptic_txs_features.csv", header=None, index_col=[1, 0])
features.index.names = ['timestamp', 'txId']

features

2         3         4          5         6    \
timestamp txId                                                           
1         230425980 -0.171469 -0.184668 -1.201369  -0.121970 -0.043875   
          5530458   -0.171484 -0.184668 -1.201369  -0.121970 -0.043875   
          232022460 -0.172107 -0.184668 -1.201369  -0.121970 -0.043875   
          232438397  0.163054  1.963790 -0.646376  12.409294 -0.063725   
          230460314  1.011523 -0.081127 -1.201369   1.153668  0.333276   
...                       ...       ...       ...        ...       ...   
49        173077460 -0.145771 -0.163752  0.463609  -0.121970 -0.043875   
          158577750 -0.165920 -0.123607  1.018602  -0.121970 -0.043875   
          158375402 -0.172014 -0.078182  1.018602   0.028105 -0.043875   
          158654197 -0.172842 -0.176622  1.018602  -0.121970 -0.043875   
          157597225 -0.012037 -0.132276  0.463609  -0.121970 -0.043875   

                          7          8         9         10        11   ...  \
timestamp txId                                                          ...   
1         230425980 -0.113002  -0.061584 -0.162097 -0.167933 -0.049707  ...   
          5530458   -0.113002  -0.061584 -0.162112 -0.167948 -0.049707  ...   
          232022460 -0.113002  -0.061584 -0.162749 -0.168576 -0.049707  ...   
          232438397  9.782742  12.414558 -0.163645 -0.115831  0.043598  ...   
          230460314  1.312656  -0.061584 -0.163523  0.041399  0.935886  ...   
...                       ...        ...       ...       ...       ...  ...   
49        173077460 -0.113002  -0.061584 -0.135803 -0.142008 -0.049707  ...   
          158577750 -0.113002  -0.061584 -0.156418 -0.162334 -0.049707  ...   
          158375402  0.054722  -0.061584 -0.163626 -0.168778 -0.045389  ...   
          158654197 -0.113002  -0.061584 -0.163501 -0.169317 -0.049707  ...   
          157597225 -0.113002  -0.061584  0.001027 -0.007095 -0.049707  ...   

                          157       158       159       160       161  \
timestamp txId                                                          
1         230425980 -0.562153 -0.600999  1.461330  1.461369  0.018279   
          5530458    0.947382  0.673103 -0.979074 -0.978556  0.018279   
          232022460  0.670883  0.439728 -0.979074 -0.978556 -0.098889   
          232438397 -0.577099 -0.613614  0.241128  0.241406  1.072793   
          230460314 -0.511871 -0.400422  0.517257  0.579382  0.018279   
...                       ...       ...       ...       ...       ...   
49        173077460 -0.577099 -0.613614  0.241128  0.241406  0.018279   
          158577750  0.162722  0.010822  1.461330  1.461369 -0.098889   
          158375402  1.261246  1.985050  1.461330  1.461369  0.018279   
          158654197 -0.397749 -0.411776  1.461330  1.461369 -0.098889   
          157597225 -0.577099 -0.613614  0.241128  0.241406 -0.098889   

                          162       163       164       165       166  
timestamp txId                                                         
1         230425980 -0.087490 -0.131155 -0.097524 -0.120613 -0.119792  
          5530458   -0.087490 -0.131155 -0.097524 -0.120613 -0.119792  
          232022460 -0.106715 -0.131155 -0.183671 -0.120613 -0.119792  
          232438397  0.085530 -0.131155  0.677799 -0.120613 -0.119792  
          230460314  0.277775  0.326394  1.293750  0.178136  0.179117  
...                       ...       ...       ...       ...       ...  
49        173077460 -0.087490 -0.131155 -0.097524 -0.120613 -0.119792  
          158577750 -0.087490 -0.084674 -0.140597 -1.760926 -1.760984  
          158375402 -0.087490 -0.131155 -0.097524 -0.120613 -0.119792  
          158654197 -0.087490 -0.084674 -0.140597  1.519700  1.521399  
          157597225 -0.087490 -0.084674 -0.140597  1.519700  1.521399  

[203769 rows x 165 columns]

In [39]:
DirG = nx.from_pandas_edgelist(edgelist, source='txId1', target='txId2', create_using=nx.DiGraph())
print(nx.is_directed(DirG))
G = DirG.to_undirected(reciprocal=False, as_view=False)
print(nx.is_directed(G))
nx.number_connected_components(G)

nx.set_node_attributes(G, classes.to_dict("index"))
keys = features.index.get_level_values(1)
rows = torch.Tensor(features.values)
dick = dict(zip(keys, rows))
nx.set_node_attributes(G, dick, "x")
print(G.nodes[230460314])


True
False
{'y': 0, 'x': tensor([ 1.0115e+00, -8.1127e-02, -1.2014e+00,  1.1537e+00,  3.3328e-01,
         1.3127e+00, -6.1584e-02, -1.6352e-01,  4.1399e-02,  9.3589e-01,
        -9.8695e-02,  1.2030e+00,  9.8890e-01,  3.4169e-01, -1.3282e-02,
        -5.7392e-02,  5.8329e-02, -3.2930e-02, -4.2709e-02,  6.5455e-02,
         3.2495e-01, -1.3973e-01, -1.4885e-01, -8.0105e-02, -1.5564e-01,
         1.3131e+00,  1.1070e+00, -1.3973e-01, -1.4885e-01, -8.0104e-02,
        -1.5564e-01,  1.3131e+00,  1.1070e+00, -2.4669e-02, -3.1272e-02,
        -2.3045e-02, -2.6215e-02,  1.4278e-03,  1.4826e-03, -2.2722e-01,
        -2.3936e-01, -7.5242e-02, -2.3495e-01, -8.6606e-01, -8.5603e-01,
        -2.2720e-01, -2.4323e-01, -9.7872e-02, -2.3590e-01, -8.7103e-01,
        -8.6108e-01, -4.1403e-01, -4.8728e-01, -2.3122e-01, -4.6727e-01,
         5.5703e-01,  7.4598e-01, -3.9151e-02, -1.7284e-01, -1.6309e-01,
        -1.6090e-01,  9.4039e-02,  2.2242e-01, -3.9146e-02, -1.7283e-01,
        -1.6308e-01, -1.60

In [46]:
S = []
attClass = nx.get_node_attributes(G, "y")
attAttributes = nx.get_node_attributes(G, "x")
for sub in nx.connected_components(G):
  s = DirG.subgraph(sub).copy()
  S.append(s)
  attrClass = dict((k, attClass[k]) for k in s.nodes)
  attrAttributes = dict((k, attAttributes[k]) for k in s.nodes)

  nx.set_node_attributes(s, attrClass, "y")
  nx.set_node_attributes(s, attrAttributes, "x")

In [47]:
kl = np.array([len(s.nodes) for s in S])
print(kl)
ind = np.argmin(kl)
print(kl[ind])
n1 = s.nodes(data=True)
print(n1)


[7880 4544 6621 5693 6803 4328 6048 4457 4996 6727 4296 2047 4528 2022
 3639 2975 3385 1976 3506 4291 3537 5894 4165 4592 2314 2523 1089 1653
 4275 2483 2816 4525 3151 2486 5507 6393 3306 2891 2760 4481 5342 7140
 5063 4975 5598 3519 5121 2954 2454]
1089
[(127262726, {'y': 0, 'x': tensor([-1.7269e-01, -1.2360e-01,  1.0186e+00, -1.2197e-01, -4.3875e-02,
        -1.1300e-01, -6.1584e-02, -1.6334e-01, -1.6916e-01, -4.9707e-02,
        -1.6565e-01, -2.8741e-02, -3.5391e-02, -4.2955e-02, -1.3282e-02,
        -5.7391e-02, -1.7085e-01, -1.7256e-01, -1.7592e-01,  8.8706e-01,
         8.8456e-01, -1.3973e-01, -1.4891e-01, -8.0147e-02, -1.5566e-01,
        -1.0763e-02, -1.2107e-02, -1.3973e-01, -1.4891e-01, -8.0147e-02,
        -1.5566e-01, -1.0669e-02, -1.2005e-02, -2.4669e-02, -3.1272e-02,
        -2.3045e-02, -2.6215e-02,  1.4278e-03,  1.4826e-03, -2.2722e-01,
        -2.3937e-01, -7.5256e-02, -2.3495e-01,  3.7468e-02,  4.3444e-02,
        -2.2720e-01, -2.4324e-01, -9.7895e-02, -2.3590e-01,  

In [50]:
color_map = {0: "grey", 1: "yellow", 2: "red"}
colors = [color_map[attrs["y"]] for _, attrs in S[ind].nodes(data=True)]
nx.draw(S[ind], node_color=colors, node_size=10)


TypeError: '_AxesStack' object is not callable

<Figure size 640x480 with 0 Axes>

In [72]:
tGraphs = [torch_geometric.utils.from_networkx(s) for s in S]
loader = torch_geometric.loader.DataLoader(tGraphs, batch_size=10, shuffle=True)

for data in loader:
    print(data)
    print(data.y)


DataBatch(x=[58097, 165], edge_index=[2, 71732], y=[58097], batch=[58097], ptr=[11])
tensor([0, 0, 0,  ..., 0, 0, 0])
DataBatch(x=[32665, 165], edge_index=[2, 35075], y=[32665], batch=[32665], ptr=[11])
tensor([0, 2, 0,  ..., 0, 0, 2])
DataBatch(x=[32525, 165], edge_index=[2, 35977], y=[32525], batch=[32525], ptr=[11])
tensor([0, 0, 0,  ..., 0, 0, 0])
DataBatch(x=[38316, 165], edge_index=[2, 43326], y=[38316], batch=[38316], ptr=[11])
tensor([0, 0, 0,  ..., 0, 0, 1])
DataBatch(x=[42166, 165], edge_index=[2, 48245], y=[42166], batch=[42166], ptr=[10])
tensor([0, 0, 0,  ..., 0, 2, 0])


In [73]:
from torch_geometric.nn import GCNConv, GCN
import torch.nn as nn
import torch.nn.functional as F


class OurGCN(torch.nn.Module):
    def __init__(self, conv_model, in_channels, hidden_channels, out_channels, num_layers):
        super(OurGCN, self).__init__()
        self.convs = nn.ModuleList()
        self.convs.append(conv_model(in_channels, hidden_channels))

        for i in range(num_layers):
            self.convs.append(conv_model(hidden_channels, hidden_channels))
        self.convs.append(conv_model(hidden_channels, out_channels))

    def forward(self, x, edge_index):
        for i in range(len(self.convs)):
            x = self.convs[i](x, edge_index)
            x = F.relu(x)
            x = F.dropout(x, training=self.training)
        return x


In [87]:
in_channels = len(features.values[0])
hidden_channels = 50
num_layers = 4
out_channels = 2
num_epoch = 100


In [88]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = GCN(in_channels,
            hidden_channels,
            out_channels, num_layers, dropout=0.5)
loss_fn = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.01)

In [89]:
# Train
from tqdm import tqdm_notebook as tqdm

def train(num_epoch):
    dataset = loader.dataset
    model.train(True)
    for epoch in tqdm(range(num_epoch), desc="Epoch"):
        total_loss = 0
        for batch in loader:
            out = model(batch.x, batch.edge_index)
            consideration_index = batch.y != 0
            loss = loss_fn(out[consideration_index], batch.y[consideration_index])
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            total_loss += loss.item() * batch.num_graphs
        avg_loss = total_loss / len(dataset)
        print(f"Epoch {epoch}, Loss: {avg_loss:.4f}")
    model.train(False)

C:\Users\aljaz\AppData\Local\Temp\ipykernel_10472\1211267009.py:6: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for epoch in tqdm(range(num_epoch), desc="Epoch"):


Epoch:   0%|          | 0/100 [00:00<?, ?it/s]

Epoch 0, Loss: 1.7439
Epoch 1, Loss: 0.4086
Epoch 2, Loss: 0.3547
Epoch 3, Loss: 0.3100
Epoch 4, Loss: 0.2796
Epoch 5, Loss: 0.2577
Epoch 6, Loss: 0.2462
Epoch 7, Loss: 0.2370
Epoch 8, Loss: 0.2330
Epoch 9, Loss: 0.2236
Epoch 10, Loss: 0.2197
Epoch 11, Loss: 0.2145
Epoch 12, Loss: 0.2118
Epoch 13, Loss: 0.2083
Epoch 14, Loss: 0.2050
Epoch 15, Loss: 0.2040
Epoch 16, Loss: 0.2018
Epoch 17, Loss: 0.1997
Epoch 18, Loss: 0.1968
Epoch 19, Loss: 0.1930
Epoch 20, Loss: 0.1929
Epoch 21, Loss: 0.1901
Epoch 22, Loss: 0.1891
Epoch 23, Loss: 0.1859
Epoch 24, Loss: 0.1856
Epoch 25, Loss: 0.1832
Epoch 26, Loss: 0.1822
Epoch 27, Loss: 0.1800
Epoch 28, Loss: 0.1778
Epoch 29, Loss: 0.1782
Epoch 30, Loss: 0.1743
Epoch 31, Loss: 0.1752
Epoch 32, Loss: 0.1737
Epoch 33, Loss: 0.1716
Epoch 34, Loss: 0.1708
Epoch 35, Loss: 0.1693
Epoch 36, Loss: 0.1666
Epoch 37, Loss: 0.1669
Epoch 38, Loss: 0.1650
Epoch 39, Loss: 0.1670
Epoch 40, Loss: 0.1644
Epoch 41, Loss: 0.1646
Epoch 42, Loss: 0.1629
Epoch 43, Loss: 0.161

KeyboardInterrupt: 

# Nov razdelek
